# Install dependencies

In [1]:
%load_ext autoreload
%autoreload 2
import sys
import plotly.io as io
io.templates.default = 'plotly_white'
# # enable modules import
# sys.path.insert(1, '/kaggle/input/modules')

# decade
decade = [1980, 1990]

# Load and preprocess data

In [2]:
from modules.spark_preprocess import SparkSPreprocessor

# SparkPreprocessor read the big csv file and convert it in the more convenient format parquet
#
sp = SparkSPreprocessor("song_lyrics.csv","./data/", "20g")


23/06/03 16:50:06 WARN Utils: Your hostname, thomas-ThinkPad-T490 resolves to a loopback address: 127.0.1.1; using 192.168.31.207 instead (on interface wlp0s20f3)
23/06/03 16:50:06 WARN Utils: Set SPARK_LOCAL_IP if you need to bind to another address
Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).
23/06/03 16:50:07 WARN NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable


In [3]:
df = sp.preprocess_data(freq=0.01, seed = 42, sample_by = 'ddecade')

In [4]:
# load data
import pandas as pd

df = pd.read_csv('./data/preprocessed_data.csv')
len(df)

4308

In [5]:
from modules.preprocess_text import clean_lyrics

df = df[df['decade'].isin(decade)]
df = clean_lyrics(df)
len(df)

1095

# Text preprocessing

In [6]:
import spacy
from modules.preprocess_text import ngram_models, ngram_preprocess

# gpu off
print("set gpu: ", spacy.prefer_gpu())

new_nlp = spacy.load('en_core_web_sm')

# get bigram_model
bigram_model, trigram_model = ngram_models(df)

# set personalised stop words
new_stop_words = {
    'like','know','come','get', 'got',
    'go','to','oh','yeah','la', 'lala', 'lalala','ooh','yeah',
    'hey','whoa','woah', 'ohh', 'was', 'mmm',
    'oooh','yah','yeh','mmm', 'hmm','deh','doh','jah','wa',
} 

set gpu:  False


# Grid search based on LDA

In [7]:
from modules.lda_models import LDATopicModeling
import logging

gensim_log = './gensim.log'

with open(gensim_log, 'w'):
    pass

# Remove all handlers associated with the root logger object.
for handler in logging.root.handlers[:]:
    logging.root.removeHandler(handler)

#initiate log file
logging.basicConfig(
    filename = gensim_log,
    filemode = 'r+',
    format='%(asctime)s:%(levelname)s:%(message)s',
    level=logging.INFO)

ngram_model = LDATopicModeling(
    df,
    gensim_log=gensim_log,
    decade = decade,
    directory = "./models/",
    lang_preprocess = lambda x : ngram_preprocess(
                        x, new_nlp, bigram_model,
                        trigram_model, new_stop_words),
    grid_search = True,
    n_topics=20,
    chunks=2000,
    worker_nodes=4)

total lda computation:  32
coherence cv:0.26626775794320423, coherence umass:-2.385091138280815
alpha:symmetric
eta:symmetric
topic:5
coherence cv:0.3459887464764611, coherence umass:-3.2107966765843634
alpha:asymmetric
eta:symmetric
topic:5
coherence cv:0.2962170961667201, coherence umass:-2.9830026810482084
alpha:symmetric
eta:symmetric
topic:6
coherence cv:0.3132522276602579, coherence umass:-2.6941937338820097
alpha:asymmetric
eta:symmetric
topic:6
coherence cv:0.2555799900092339, coherence umass:-2.585950767164519
alpha:symmetric
eta:symmetric
topic:7
coherence cv:0.3083829771705017, coherence umass:-2.9809536257556744
alpha:asymmetric
eta:symmetric
topic:7
coherence cv:0.310723395859646, coherence umass:-3.1634219069318696
alpha:symmetric
eta:symmetric
topic:8
coherence cv:0.29220207895849926, coherence umass:-3.380749187489823
alpha:asymmetric
eta:symmetric
topic:8
coherence cv:0.29810529195831675, coherence umass:-3.2530217774665173
alpha:symmetric
eta:symmetric
topic:9
coheren

In [8]:
ngram_model.plot_tsne(2)

[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Indexed 1095 samples in 0.000s...
[t-SNE] Computed neighbors for 1095 samples in 0.189s...
[t-SNE] Computed conditional probabilities for sample 1000 / 1095
[t-SNE] Computed conditional probabilities for sample 1095 / 1095
[t-SNE] Mean sigma: 0.022038
[t-SNE] KL divergence after 250 iterations with early exaggeration: 54.734928
[t-SNE] KL divergence after 1000 iterations: 0.386103


In [9]:
ngram_model.dashboard_LDAvis()

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
13     0.173007 -0.009530       1        1  14.244489
7      0.127970  0.045553       2        1   7.967437
17     0.058876  0.039010       3        1   7.818732
3     -0.131872  0.096518       4        1   6.878104
16    -0.003282 -0.014853       5        1   5.871100
2      0.004613 -0.034943       6        1   5.735403
18    -0.108720  0.134416       7        1   4.952002
19     0.098861  0.162259       8        1   4.936190
5      0.035484 -0.082503       9        1   4.228657
4     -0.065770 -0.019317      10        1   3.959469
1      0.068367  0.054162      11        1   3.892130
12     0.003265 -0.082721      12        1   3.886802
15    -0.044615 -0.037313      13        1   3.847493
10    -0.057748  0.019795      14        1   3.524507
8     -0.029197 -0.041621      15        1   3.374918
6     -0.068022 -0.002273      16        1   3.356771
11     0.005081 -0.114741      17        1   3.286032
0      0.028682 -0.042880      18        1   2.944929
9     -0.051734 -0.011375      19        1   2.935100
14    -0.043246 -0.057643      20        1   2.359736, topic_info=        Term         Freq        Total Category  logprob  loglift
204     love  1418.000000  1418.000000  Default  30.0000  30.0000
120     baby   614.000000   614.000000  Default  29.0000  29.0000
291     away   486.000000   486.000000  Default  28.0000  28.0000
221   niggas   262.000000   262.000000  Default  27.0000  27.0000
214     mind   347.000000   347.000000  Default  26.0000  26.0000
...      ...          ...          ...      ...      ...      ...
291     away     6.578073   486.868504  Topic20  -5.4725  -0.5576
1105   storm     4.737379    36.050687  Topic20  -5.8007   1.7172
761   nothin     4.857857    49.705207  Topic20  -5.7756   1.4211
77     right     5.470181   379.526640  Topic20  -5.6569  -0.4930
25     cause     5.177959   329.792642  Topic20  -5.7118  -0.4074

[1382 rows x 6 columns], token_table=      Topic      Freq      Term
term                           
5046      9  0.875234   absence
9020     17  0.718491  absolute
3528     10  0.147951     abyss
3528     12  0.813729     abyss
1520      2  0.232035    action
...     ...       ...       ...
3108     12  0.029292     youth
3108     13  0.029292     youth
3108     16  0.029292     youth
3108     19  0.058585     youth
8520      1  0.845151     yucky

[4871 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[14, 8, 18, 4, 17, 3, 19, 20, 6, 5, 2, 13, 16, 11, 9, 7, 12, 1, 10, 15])

In [10]:
ngram_model.plot_likelihood(30)

In [11]:
ngram_model.plot_coherence()

In [12]:
ngram_model.get_cv_results

topics       alpha        eta       c_v    u_mass
0        5   symmetric  symmetric  0.266268 -2.385091
1        5  asymmetric  symmetric  0.345989 -3.210797
2        6   symmetric  symmetric  0.296217 -2.983003
3        6  asymmetric  symmetric  0.313252 -2.694194
4        7   symmetric  symmetric  0.255580 -2.585951
5        7  asymmetric  symmetric  0.308383 -2.980954
6        8   symmetric  symmetric  0.310723 -3.163422
7        8  asymmetric  symmetric  0.292202 -3.380749
8        9   symmetric  symmetric  0.298105 -3.253022
9        9  asymmetric  symmetric  0.310806 -3.724868
10      10   symmetric  symmetric  0.314038 -3.670629
11      10  asymmetric  symmetric  0.328977 -4.393525
12      11   symmetric  symmetric  0.290239 -4.299903
13      11  asymmetric  symmetric  0.346214 -4.516795
14      12   symmetric  symmetric  0.326530 -4.267875
15      12  asymmetric  symmetric  0.297534 -3.903602
16      13   symmetric  symmetric  0.297706 -3.824862
17      13  asymmetric  symmetric  0.333537 -4.738164
18      14   symmetric  symmetric  0.323724 -4.359003
19      14  asymmetric  symmetric  0.314153 -4.393912
20      15   symmetric  symmetric  0.316346 -4.408414
21      15  asymmetric  symmetric  0.342382 -4.352723
22      16   symmetric  symmetric  0.313537 -4.135458
23      16  asymmetric  symmetric  0.323294 -4.649561
24      17   symmetric  symmetric  0.329182 -4.450718
25      17  asymmetric  symmetric  0.326722 -4.844780
26      18   symmetric  symmetric  0.350208 -5.164092
27      18  asymmetric  symmetric  0.313130 -4.151539
28      19   symmetric  symmetric  0.321321 -4.532832
29      19  asymmetric  symmetric  0.339192 -4.926947
30      20   symmetric  symmetric  0.357681 -5.547453
31      20  asymmetric  symmetric  0.322522 -4.895014

In [13]:
ngram_model.dashboard()

[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Indexed 1095 samples in 0.000s...
[t-SNE] Computed neighbors for 1095 samples in 0.158s...
[t-SNE] Computed conditional probabilities for sample 1000 / 1095
[t-SNE] Computed conditional probabilities for sample 1095 / 1095
[t-SNE] Mean sigma: 0.022037
[t-SNE] KL divergence after 250 iterations with early exaggeration: 54.588524
[t-SNE] KL divergence after 1000 iterations: 0.389059


In [14]:
ngram_model.save_current_model()

# U_MASS Coherence grid search

In [15]:
ngram_model = LDATopicModeling(
    df,
    gensim_log=gensim_log,
    decade = decade,
    lang_preprocess = lambda x : ngram_preprocess(
                        x, new_nlp, bigram_model,
                        trigram_model, new_stop_words),
    grid_search = True,
    n_topics=20,
    chunks=2000,
    directory = "./models/",
    metric='u_mass',
    worker_nodes=4)

total lda computation:  32
coherence cv:0.3212332926334624, coherence umass:-2.537261163077799
alpha:symmetric
eta:symmetric
topic:5
coherence cv:0.27929165548103674, coherence umass:-2.541326152114862
alpha:asymmetric
eta:symmetric
topic:5
coherence cv:0.2480469302769439, coherence umass:-2.3259676249008487
alpha:symmetric
eta:symmetric
topic:6
coherence cv:0.2998066375898555, coherence umass:-2.563849397725305
alpha:asymmetric
eta:symmetric
topic:6
coherence cv:0.32143996053316354, coherence umass:-3.834739818212864
alpha:symmetric
eta:symmetric
topic:7
coherence cv:0.2698165156715153, coherence umass:-2.5819810120891695
alpha:asymmetric
eta:symmetric
topic:7
coherence cv:0.2630723300510288, coherence umass:-3.198287766449436
alpha:symmetric
eta:symmetric
topic:8
coherence cv:0.297259087993039, coherence umass:-3.012206747015346
alpha:asymmetric
eta:symmetric
topic:8
coherence cv:0.305128568523609, coherence umass:-3.37241564087471
alpha:symmetric
eta:symmetric
topic:9
coherence cv:0

In [16]:
ngram_model.plot_tsne(2)

[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Indexed 1095 samples in 0.001s...
[t-SNE] Computed neighbors for 1095 samples in 0.019s...
[t-SNE] Computed conditional probabilities for sample 1000 / 1095
[t-SNE] Computed conditional probabilities for sample 1095 / 1095
[t-SNE] Mean sigma: 0.003274
[t-SNE] KL divergence after 250 iterations with early exaggeration: 54.809528
[t-SNE] KL divergence after 1000 iterations: 0.304494


In [17]:
ngram_model.dashboard_LDAvis()

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
5      0.106945  0.018510       1        1  23.596873
2     -0.026645 -0.032858       2        1  23.033926
4     -0.044064  0.029220       3        1  18.115989
0     -0.069365  0.129707       4        1  12.950807
1      0.122665 -0.025992       5        1  12.719970
3     -0.089537 -0.118587       6        1   9.582436, topic_info=        Term         Freq        Total Category  logprob  loglift
204     love  1293.000000  1293.000000  Default  30.0000  30.0000
120     baby   625.000000   625.000000  Default  29.0000  29.0000
221   niggas   260.000000   260.000000  Default  28.0000  28.0000
48      girl   328.000000   328.000000  Default  27.0000  27.0000
1086   heart   328.000000   328.000000  Default  26.0000  26.0000
...      ...          ...          ...      ...      ...      ...
152    dream    21.936394   190.605955   Topic6  -5.6694   0.1832
104     time    26.524979   903.830615   Topic6  -5.4795  -1.1833
13     thing    23.263369   382.928458   Topic6  -5.6107  -0.4557
298    night    22.747188   482.709780   Topic6  -5.6331  -0.7097
291     away    21.220104   496.920727   Topic6  -5.7026  -0.8082

[477 rows x 6 columns], token_table=      Topic      Freq      Term
term                           
3528      4  0.076396     abyss
3528      6  0.840355     abyss
5812      4  0.975748      agua
3908      5  0.793608  alliance
5542      5  0.121939  almighty
...     ...       ...       ...
3108      1  0.088723     youth
3108      2  0.147871     youth
3108      3  0.621060     youth
3108      4  0.088723     youth
3108      5  0.059149     youth

[1065 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[6, 3, 5, 1, 2, 4])

In [18]:
ngram_model.plot_likelihood(30)

In [19]:
ngram_model.plot_coherence()

In [20]:
ngram_model.get_cv_results

topics       alpha        eta       c_v    u_mass
0        5   symmetric  symmetric  0.321233 -2.537261
1        5  asymmetric  symmetric  0.279292 -2.541326
2        6   symmetric  symmetric  0.248047 -2.325968
3        6  asymmetric  symmetric  0.299807 -2.563849
4        7   symmetric  symmetric  0.321440 -3.834740
5        7  asymmetric  symmetric  0.269817 -2.581981
6        8   symmetric  symmetric  0.263072 -3.198288
7        8  asymmetric  symmetric  0.297259 -3.012207
8        9   symmetric  symmetric  0.305129 -3.372416
9        9  asymmetric  symmetric  0.319656 -3.726587
10      10   symmetric  symmetric  0.289834 -3.507007
11      10  asymmetric  symmetric  0.334960 -4.158091
12      11   symmetric  symmetric  0.295780 -3.862676
13      11  asymmetric  symmetric  0.324779 -4.478890
14      12   symmetric  symmetric  0.292981 -3.771956
15      12  asymmetric  symmetric  0.302333 -4.241982
16      13   symmetric  symmetric  0.321267 -3.794274
17      13  asymmetric  symmetric  0.320408 -4.564780
18      14   symmetric  symmetric  0.334789 -4.661389
19      14  asymmetric  symmetric  0.360870 -5.350260
20      15   symmetric  symmetric  0.324696 -4.468510
21      15  asymmetric  symmetric  0.313020 -4.038896
22      16   symmetric  symmetric  0.311402 -4.466887
23      16  asymmetric  symmetric  0.333960 -4.912069
24      17   symmetric  symmetric  0.306254 -4.118445
25      17  asymmetric  symmetric  0.328746 -4.793351
26      18   symmetric  symmetric  0.336522 -4.611627
27      18  asymmetric  symmetric  0.360937 -5.531112
28      19   symmetric  symmetric  0.341240 -5.380085
29      19  asymmetric  symmetric  0.353035 -5.961555
30      20   symmetric  symmetric  0.347029 -5.136548
31      20  asymmetric  symmetric  0.350043 -5.567229

In [21]:
ngram_model.dashboard()

[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Indexed 1095 samples in 0.001s...
[t-SNE] Computed neighbors for 1095 samples in 0.022s...
[t-SNE] Computed conditional probabilities for sample 1000 / 1095
[t-SNE] Computed conditional probabilities for sample 1095 / 1095
[t-SNE] Mean sigma: 0.003270
[t-SNE] KL divergence after 250 iterations with early exaggeration: 54.334614
[t-SNE] KL divergence after 1000 iterations: 0.301103


In [22]:
ngram_model.save_current_model()

# Bertopic

Preprocess data before clustering (not advised by documentation).

In [23]:
# lyrics preprocessing
preprocess_lyrics = df['lyrics'] \
    .apply(lambda x : ' '.join(
            ngram_preprocess(
            x, new_nlp, bigram_model, 
            trigram_model, new_stop_words)))

# clean lyrics
docs = preprocess_lyrics.values

In [24]:
from sentence_transformers import SentenceTransformer
from bertopic import BERTopic
from hdbscan import HDBSCAN
from umap import UMAP

sentence_model = SentenceTransformer("all-MiniLM-L6-v2")
embeddings = sentence_model.encode(docs)

umap_model = UMAP(n_components=5, n_neighbors=15, min_dist=0.0)
hdbscan_model = HDBSCAN(min_samples=10, gen_min_span_tree=True)

# Train BERTopic
topic_model = BERTopic(nr_topics = 30, umap_model=umap_model, hdbscan_model=hdbscan_model).fit(docs, embeddings)

/home/thomas/miniconda3/envs/genius-env/lib/python3.10/site-packages/umap/distances.py:1063: NumbaDeprecationWarning:

The 'nopython' keyword argument was not supplied to the 'numba.jit' decorator. The implicit default value for this argument is currently False, but it will be changed to True in Numba 0.59.0. See https://numba.readthedocs.io/en/stable/reference/deprecation.html#deprecation-of-object-mode-fall-back-behaviour-when-using-jit for details.

/home/thomas/miniconda3/envs/genius-env/lib/python3.10/site-packages/umap/distances.py:1071: NumbaDeprecationWarning:

The 'nopython' keyword argument was not supplied to the 'numba.jit' decorator. The implicit default value for this argument is currently False, but it will be changed to True in Numba 0.59.0. See https://numba.readthedocs.io/en/stable/reference/deprecation.html#deprecation-of-object-mode-fall-back-behaviour-when-using-jit for details.

/home/thomas/miniconda3/envs/genius-env/lib/python3.10/site-packages/umap/distances.py

Batches:   0%|          | 0/35 [00:00<?, ?it/s]

In [25]:
# Run the visualization with the original embeddings
topic_model.visualize_documents(docs, embeddings=embeddings)

# Reduce dimensionality of embeddings, this step is optional but much faster to perform iteratively:
reduced_embeddings = UMAP(n_neighbors=10, n_components=2, min_dist=0.0, metric='cosine').fit_transform(embeddings)

In [26]:
topic_model.visualize_documents(docs,reduced_embeddings=reduced_embeddings)

In [27]:
topic_model.visualize_topics()

In [28]:
topic_model.visualize_hierarchy()

/home/thomas/miniconda3/envs/genius-env/lib/python3.10/site-packages/plotly/figure_factory/_dendrogram.py:350: DeprecationWarning:

scipy.array is deprecated and will be removed in SciPy 2.0.0, use numpy.array instead

/home/thomas/miniconda3/envs/genius-env/lib/python3.10/site-packages/plotly/figure_factory/_dendrogram.py:351: DeprecationWarning:

scipy.array is deprecated and will be removed in SciPy 2.0.0, use numpy.array instead

/home/thomas/miniconda3/envs/genius-env/lib/python3.10/site-packages/plotly/figure_factory/_dendrogram.py:352: DeprecationWarning:

scipy.array is deprecated and will be removed in SciPy 2.0.0, use numpy.array instead

/home/thomas/miniconda3/envs/genius-env/lib/python3.10/site-packages/plotly/figure_factory/_dendrogram.py:353: DeprecationWarning:

scipy.array is deprecated and will be removed in SciPy 2.0.0, use numpy.array instead



In [29]:
topic_model.visualize_barchart()

In [30]:
topic_model.visualize_heatmap()

In [31]:
topic_model.visualize_term_rank()

In [32]:
from modules.bertopic_models import compute_coherence

print('cv :',compute_coherence(topic_model, docs, topic_model.topics_, metric = 'c_v'))
print('umass :',compute_coherence(topic_model, docs, topic_model.topics_, metric = 'u_mass'))

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The 

In [33]:
topics_per_class = topic_model.topics_per_class(docs, classes=df['tag'].tolist())
topic_model.visualize_topics_per_class(topics_per_class)

In [34]:
from modules.bertopic_models import save_bertopic_model

save_bertopic_model(topic_model, filename = 'bertopic_prepro_', model_dir = "./models")

In [35]:
from sklearn.feature_extraction.text import CountVectorizer

docs = df['lyrics'].values

# apply embeddings to doc
embeddings = sentence_model.encode(docs)

# Train BERTopic
vectorizer_model = CountVectorizer(
    stop_words=list(new_nlp.Defaults.stop_words | new_stop_words))

# Train BERTopic
topic_model = BERTopic(nr_topics = 30,vectorizer_model=vectorizer_model, umap_model=umap_model, hdbscan_model=hdbscan_model).fit(docs, embeddings)

Batches:   0%|          | 0/35 [00:00<?, ?it/s]

In [36]:
# Run the visualization with the original embeddings
topic_model.visualize_documents(docs, embeddings=embeddings)

# Reduce dimensionality of embeddings, this step is optional but much faster to perform iteratively:
reduced_embeddings = UMAP(n_neighbors=10, n_components=2, min_dist=0.0, metric='cosine').fit_transform(embeddings)

In [37]:
topic_model.visualize_documents(docs, reduced_embeddings=reduced_embeddings)

In [38]:
topic_model.visualize_topics()

In [39]:
topic_model.visualize_hierarchy()

/home/thomas/miniconda3/envs/genius-env/lib/python3.10/site-packages/plotly/figure_factory/_dendrogram.py:350: DeprecationWarning:

scipy.array is deprecated and will be removed in SciPy 2.0.0, use numpy.array instead

/home/thomas/miniconda3/envs/genius-env/lib/python3.10/site-packages/plotly/figure_factory/_dendrogram.py:351: DeprecationWarning:

scipy.array is deprecated and will be removed in SciPy 2.0.0, use numpy.array instead

/home/thomas/miniconda3/envs/genius-env/lib/python3.10/site-packages/plotly/figure_factory/_dendrogram.py:352: DeprecationWarning:

scipy.array is deprecated and will be removed in SciPy 2.0.0, use numpy.array instead

/home/thomas/miniconda3/envs/genius-env/lib/python3.10/site-packages/plotly/figure_factory/_dendrogram.py:353: DeprecationWarning:

scipy.array is deprecated and will be removed in SciPy 2.0.0, use numpy.array instead



In [40]:
topic_model.visualize_barchart()

In [41]:
topic_model.visualize_heatmap()

In [42]:
topic_model.visualize_term_rank()

In [43]:
print('cv :',compute_coherence(topic_model, docs, topic_model.topics_, metric = 'c_v'))
print('umass :',compute_coherence(topic_model, docs, topic_model.topics_, metric = 'u_mass'))

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The 

In [44]:
topics_per_class = topic_model.topics_per_class(docs, classes=df['tag'].tolist())
topic_model.visualize_topics_per_class(topics_per_class)

In [45]:
save_bertopic_model(topic_model, filename = 'bertopic_', model_dir = "./models")

In [46]:
from sklearn import preprocessing
le = preprocessing.LabelEncoder()

le.fit(sorted(df['tag'].unique()))

y = le.transform(df['tag'].tolist())


In [47]:
from bertopic.vectorizers import ClassTfidfTransformer

ctfidf_model = ClassTfidfTransformer(reduce_frequent_words=True)

topic_model = BERTopic(nr_topics = 30, verbose=True, ctfidf_model=ctfidf_model,
                       umap_model=umap_model, hdbscan_model=hdbscan_model).fit(docs, y=y, embeddings = embeddings)

2023-06-03 17:18:08,304 - BERTopic - Reduced dimensionality
2023-06-03 17:18:08,332 - BERTopic - Clustered reduced embeddings
2023-06-03 17:18:08,652 - BERTopic - Reduced number of topics from 6 to 6


In [48]:
# Run the visualization with the original embeddings
topic_model.visualize_documents(docs, embeddings=embeddings)

# Reduce dimensionality of embeddings, this step is optional but much faster to perform iteratively:
reduced_embeddings = UMAP(n_neighbors=10, n_components=2, min_dist=0.0, metric='cosine').fit_transform(embeddings)

In [49]:
topic_model.visualize_documents(docs, reduced_embeddings=reduced_embeddings)

In [50]:
topic_model.visualize_hierarchy()

/home/thomas/miniconda3/envs/genius-env/lib/python3.10/site-packages/plotly/figure_factory/_dendrogram.py:350: DeprecationWarning:

scipy.array is deprecated and will be removed in SciPy 2.0.0, use numpy.array instead

/home/thomas/miniconda3/envs/genius-env/lib/python3.10/site-packages/plotly/figure_factory/_dendrogram.py:351: DeprecationWarning:

scipy.array is deprecated and will be removed in SciPy 2.0.0, use numpy.array instead

/home/thomas/miniconda3/envs/genius-env/lib/python3.10/site-packages/plotly/figure_factory/_dendrogram.py:352: DeprecationWarning:

scipy.array is deprecated and will be removed in SciPy 2.0.0, use numpy.array instead

/home/thomas/miniconda3/envs/genius-env/lib/python3.10/site-packages/plotly/figure_factory/_dendrogram.py:353: DeprecationWarning:

scipy.array is deprecated and will be removed in SciPy 2.0.0, use numpy.array instead



In [51]:
topic_model.visualize_topics()

In [52]:
topic_model.visualize_barchart()

In [53]:
topic_model.visualize_heatmap()

In [54]:
topic_model.visualize_term_rank()

In [55]:
topics_per_class = topic_model.topics_per_class(docs, classes=df['tag'].tolist())
topic_model.visualize_topics_per_class(topics_per_class)

5it [00:00, 21.86it/s]


In [56]:
print('cv :',compute_coherence(topic_model, docs, topic_model.topics_, metric = 'c_v'))
print('umass :',compute_coherence(topic_model, docs, topic_model.topics_, metric = 'u_mass'))

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The 

In [57]:
save_bertopic_model(topic_model, filename = 'bertopic_semsup_', model_dir = "./working/models")

# Bertopic with brunokreiner lyrics transformer

In [58]:
from sentence_transformers import SentenceTransformer

lyrics_model = SentenceTransformer('brunokreiner/lyrics-bert')

# apply embeddings to doc
embeddings = lyrics_model.encode(docs)

# Train BERTopic
vectorizer_model = CountVectorizer(
    stop_words=list(new_nlp.Defaults.stop_words | new_stop_words))
topic_model = BERTopic(nr_topics = 30, vectorizer_model=vectorizer_model, umap_model=umap_model, hdbscan_model=hdbscan_model).fit(docs, embeddings)

Batches:   0%|          | 0/35 [00:00<?, ?it/s]

2023-06-03 17:18:51,781 - BERTopic - Reduced dimensionality
2023-06-03 17:18:51,815 - BERTopic - Clustered reduced embeddings
2023-06-03 17:18:52,174 - BERTopic - Reduced number of topics from 3 to 3


In [59]:
# Run the visualization with the original embeddings
topic_model.visualize_documents(docs, embeddings=embeddings)

# Reduce dimensionality of embeddings, this step is optional but much faster to perform iteratively:
reduced_embeddings = UMAP(n_neighbors=10, n_components=2, min_dist=0.0, metric='cosine').fit_transform(embeddings)

In [60]:
topic_model.visualize_documents(docs, reduced_embeddings=reduced_embeddings)

In [61]:
topic_model.visualize_topics()

ValueError: zero-size array to reduction operation maximum which has no identity

In [62]:
topic_model.visualize_barchart()

In [63]:
topics_per_class = topic_model.topics_per_class(docs, classes=df['tag'].tolist())
topic_model.visualize_topics_per_class(topics_per_class)

In [64]:
print('cv :',compute_coherence(topic_model, docs, topic_model.topics_, metric = 'c_v'))
print('umass :',compute_coherence(topic_model, docs, topic_model.topics_, metric = 'u_mass'))

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The 

In [65]:
save_bertopic_model(topic_model, filename = 'bertopic_lyricsBert_', model_dir = "./models")